In [1]:
import numpy as np
import matplotlib.pyplot as plt
import time
import pandas as pd
import math
import random
import pickle

In [2]:
# # Open the input file and output file in the same context
# with open('llmrawdata.txt', 'r') as infile, open('lmprocesseddata.txt', 'w') as outfile:
#     for line in infile:
#         if 'l4s_ecn_marking-start' in line:
#             # Remove the prefix 'l4s_ecn_marking-start,' and trailing ' end'
#             temp=line.split("-")
#             temp1=temp[1]
            
#             temp1=temp1.split(",")
#             #print(temp1[-1]=="end \n")
#             if(temp1[-1]=="end \n"):
#                 outfile.writelines(temp[1])


In [3]:
# Open the input file and output file in the same context
with open('llmrawdata.txt', 'r') as infile, open('lmprocesseddata.txt', 'w') as outfile:
    for line in infile:
        if 'l4s_ecn_marking-start' in line:
            # Remove the prefix 'l4s_ecn_marking-start,' and trailing ' end'
            parts = line.split("-")
            if len(parts) > 1:
                content = parts[1].strip()  # Remove any leading/trailing whitespace
                if content.endswith('end'):
                    # Write the content to the output file, stripping the 'end' part
                    outfile.write(content[6:-4] + '\n')


In [4]:
column_list = [
    "queue_type",                   # q->queue_type
    "qdelay_reference",             # pprms->qdelay_ref
    "tupdate",                      # pprms->tupdate
    "max_burst",                    # pprms->max_burst
    "max_ecn_threshold",            # pprms->max_ecnth
    "alpha_coefficient",            # pprms->alpha
    "beta_coefficient",             # pprms->beta
    "flags",                        # pprms->flags
    "burst_allowance",              # pst->burst_allowance
    "drop_probability",             # pst->drop_prob
    "current_queue_delay",          # pst->current_qdelay
    "previous_queue_delay",         # pst->qdelay_old
    "accumulated_probability",      # pst->accu_prob
    "measurement_start_time",       # pst->measurement_start
    "average_dequeue_time",         # pst->avg_dq_time
    "dequeue_count",                # pst->dq_count
    "status_flags",                 # pst->sflags
    "total_packets",                # q->stats.tot_pkts
    "total_bytes",                  # q->stats.tot_bytes
    "queue_length",                 # q->stats.length
    "length_in_bytes",              # q->stats.len_bytes
    "total_drops",                  # q->stats.drops
    "dequeue_action",               # dequeue_action
]


In [5]:
df=pd.read_csv("lmprocesseddata.txt",names=column_list,header=None)

# Drop columns that contain 'pprms' in their name
columns_to_drop = [
    "qdelay_reference",             # pprms->qdelay_ref
    "tupdate",                      # pprms->tupdate
    "max_burst",                    # pprms->max_burst
    "max_ecn_threshold",            # pprms->max_ecnth
    "alpha_coefficient",            # pprms->alpha
    "beta_coefficient",             # pprms->beta
    "flags",                        # pprms->flags
    ]
df = df.drop(columns=columns_to_drop)

df["total_bytes"] = df["total_bytes"].astype(int)
df["measurement_start_time"] = df["measurement_start_time"].astype(int)
df["current_queue_delay"] = df["current_queue_delay"].astype(int)



In [6]:
# df[df['current_queue_delay'] == 0]
# (df.shape[0] - df[df['current_queue_delay'] == 0].shape[0]) / df.shape[0]
# (df[df['current_queue_delay'] == 0].shape[0]) / df.shape[0]

In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 721858 entries, 0 to 721857
Data columns (total 16 columns):
 #   Column                   Non-Null Count   Dtype
---  ------                   --------------   -----
 0   queue_type               721858 non-null  int64
 1   burst_allowance          721858 non-null  int64
 2   drop_probability         721858 non-null  int64
 3   current_queue_delay      721858 non-null  int32
 4   previous_queue_delay     721858 non-null  int64
 5   accumulated_probability  721858 non-null  int64
 6   measurement_start_time   721858 non-null  int32
 7   average_dequeue_time     721858 non-null  int64
 8   dequeue_count            721858 non-null  int64
 9   status_flags             721858 non-null  int64
 10  total_packets            721858 non-null  int64
 11  total_bytes              721858 non-null  int32
 12  queue_length             721858 non-null  int64
 13  length_in_bytes          721858 non-null  int64
 14  total_drops              721858 non-

In [8]:
df.columns.to_list()

['queue_type',
 'burst_allowance',
 'drop_probability',
 'current_queue_delay',
 'previous_queue_delay',
 'accumulated_probability',
 'measurement_start_time',
 'average_dequeue_time',
 'dequeue_count',
 'status_flags',
 'total_packets',
 'total_bytes',
 'queue_length',
 'length_in_bytes',
 'total_drops',
 'dequeue_action']

In [9]:
# import pandas as pd
# import numpy as np
# import math

# # Initialize new columns with zeros
# df["bytes_sent"] = 0.00


# # Initialize previous_total_bytes
# previous_total_bytes = 0

# # Iterate over each entry in data
# for index, row in df.iterrows():
#     # Get current total_bytes
#     current_total_bytes = row["total_bytes"]
#     # Calculate bytes_sent
#     bytes_sent = current_total_bytes - previous_total_bytes
#     df.at[index, "bytes_sent"] = bytes_sent
    
#     # Update previous_total_bytes for the next iteration
#     if current_total_bytes !=0:
#         previous_total_bytes = current_total_bytes


In [10]:
# import pandas as pd
# import numpy as np
# import math

# # Initialize new columns with zeros
# df["bytes_sent"] = 0.00
# df["instantaneous_throughput"] = 0.00
# df["reward"] = 0.00

# # Initialize previous_total_bytes
# previous_total_bytes = 0

# # Iterate over each entry in data
# for index, row in df.iterrows():
#     # Get current total_bytes
#     current_total_bytes = row["total_bytes"]
#     # Calculate bytes_sent
#     bytes_sent = current_total_bytes - previous_total_bytes
#     df.at[index, "bytes_sent"] = bytes_sent
    
#     # Update previous_total_bytes for the next iteration
#     previous_total_bytes = current_total_bytes
    
#     # Calculate instantaneous_throughput
#     if row["current_queue_delay"] == 0:
#         instantaneous_throughput = -1
#     else:
#         instantaneous_throughput = bytes_sent / row["current_queue_delay"]
#     df.at[index, "instantaneous_throughput"] = instantaneous_throughput
    
#     # Calculate reward
#     if instantaneous_throughput > 0:
#         reward = math.log10(instantaneous_throughput)
#     else:
#         reward = 0  # Using negative infinity to represent an undefined reward
#     df.at[index, "reward"] = reward


In [11]:

class ExperiencePool:
    """
    Experience pool for collecting trajectories.
    """
    def __init__(self):
        self.states = []
        self.actions = []
        self.rewards = []
        self.dones = []

    def add(self, state, action, reward, done):
        
        self.states.append(state)  # sometime state is also called obs (observation)
        self.actions.append(action)
        self.rewards.append(reward)
        self.dones.append(done)

    def __len__(self):
        return len(self.states)


In [12]:
import numpy as np
import pandas as pd

# Define the batch size
K = 10

# Create an instance of ExperiencePool
exp_pool = ExperiencePool()

# Sample DataFrame for demonstration (replace with your actual DataFrame)
# df = pd.read_csv('your_data.csv')  # or however you load your DataFrame

# Iterate through the DataFrame in chunks of K rows
for start in range(0, len(df), K):
    end = min(start + K, len(df))  # Ensure the end index does not exceed the DataFrame length
    batch_df = df.iloc[start:end]

    # Extract feature columns
    queue_type = batch_df['queue_type'].values
    burst_allowance = batch_df['burst_allowance'].values
    drop_probability = batch_df['drop_probability'].values
    current_queue_delay = batch_df['current_queue_delay'].values
    previous_queue_delay = batch_df['previous_queue_delay'].values
    accumulated_probability = batch_df['accumulated_probability'].values
    measurement_start_time = batch_df['measurement_start_time'].values
    average_dequeue_time = batch_df['average_dequeue_time'].values
    dequeue_count = batch_df['dequeue_count'].values
    status_flags = batch_df['status_flags'].values
    total_packets = batch_df['total_packets'].values
    total_bytes = batch_df['total_bytes'].values
    queue_length = batch_df['queue_length'].values
    length_in_bytes = batch_df['length_in_bytes'].values
    total_drops = batch_df['total_drops'].values

    # Organize into the state format
    states_batch = np.array([
        queue_type,
        burst_allowance,
        drop_probability,
        current_queue_delay,
        previous_queue_delay,
        accumulated_probability,
        measurement_start_time,
        average_dequeue_time,
        dequeue_count,
        status_flags,
        total_packets,
        total_bytes,
        queue_length,
        length_in_bytes,
        total_drops
    ]).T  # Transpose to get the right shape (K x num_features)

    actions_batch = batch_df['dequeue_action'].tolist()
    rewards_batch = batch_df['current_queue_delay'].tolist()
    dones_batch = [0] * len(batch_df)  # Assuming 'done' is 0 for all entries

    # Add the accumulated batch to the experience pool
    for state, action, reward, done in zip(states_batch, actions_batch, rewards_batch, dones_batch):
        exp_pool.add(state=state, action=action, reward=reward, done=done)

    # Optional: Print or log the status after processing each batch
    print(f"Processed batch from row {start} to {end}, pool size: {len(exp_pool)}")


Processed batch from row 0 to 10, pool size: 10
Processed batch from row 10 to 20, pool size: 20
Processed batch from row 20 to 30, pool size: 30
Processed batch from row 30 to 40, pool size: 40
Processed batch from row 40 to 50, pool size: 50
Processed batch from row 50 to 60, pool size: 60
Processed batch from row 60 to 70, pool size: 70
Processed batch from row 70 to 80, pool size: 80
Processed batch from row 80 to 90, pool size: 90
Processed batch from row 90 to 100, pool size: 100
Processed batch from row 100 to 110, pool size: 110
Processed batch from row 110 to 120, pool size: 120
Processed batch from row 120 to 130, pool size: 130
Processed batch from row 130 to 140, pool size: 140
Processed batch from row 140 to 150, pool size: 150
Processed batch from row 150 to 160, pool size: 160
Processed batch from row 160 to 170, pool size: 170
Processed batch from row 170 to 180, pool size: 180
Processed batch from row 180 to 190, pool size: 190
Processed batch from row 190 to 200, pool

In [13]:
# import numpy as np
# import pandas as pd

# # Define the batch size
# K = 10

# # Create an instance of ExperiencePool
# exp_pool = ExperiencePool()

# # Sample DataFrame for demonstration (replace with your actual DataFrame)
# # df = pd.read_csv('your_data.csv')  # or however you load your DataFrame

# # Iterate through the DataFrame in chunks of K rows
# for start in range(0, len(df), K):
#     end = min(start + K, len(df))  # Ensure the end index does not exceed the DataFrame length
#     batch_df = df.iloc[start:end]

#     # Collect data for the current batch
#     states_batch = np.array(batch_df.drop(columns=['dequeue_action', 'current_queue_delay'])).tolist()
#     actions_batch = batch_df['dequeue_action'].tolist()
#     rewards_batch = batch_df['current_queue_delay'].tolist()
#     dones_batch = [0] * len(batch_df)  # Assuming 'done' is 0 for all entries

#     # Add the accumulated batch to the experience pool
#     for state, action, reward, done in zip(states_batch, actions_batch, rewards_batch, dones_batch):
#         exp_pool.add(state=state, action=action, reward=reward, done=done)

#     # Optional: Print or log the status after processing each batch
#     print(f"Processed batch from row {start} to {end}, pool size: {len(exp_pool)}")


In [14]:
pickle_save_path='exp_pool_l4s.pkl'
pickle.dump(exp_pool, open( pickle_save_path, 'wb'))
print(f"Done. Experience pool saved at:", pickle_save_path)

Done. Experience pool saved at: exp_pool_l4s.pkl


In [15]:
np.array(exp_pool.states[0]).shape

(15,)

In [16]:
exp_pool_load=pickle.load(open( pickle_save_path, 'rb'))